In [1]:
import pandas as pd
import numpy as np
import pickle
import datetime
import gzip
from sklearn.tree import DecisionTreeClassifier
from sklearn.metrics import f1_score
from sklearn.metrics import jaccard_similarity_score

from multilabelexplanations import distance_functions
from multilabelexplanations import rules
from multilabelexplanations import synthetic_neighborhood
import json

In [2]:
%pylab inline

Populating the interactive namespace from numpy and matplotlib


In [3]:
#lista dei nomi dei dataset
dataset_list = ['yeast']

#lista contenente i prefissi delle colonne dei dataframe che contengono le classi da predire
columns_ylist = ['Class']

#dizionario con chiave nome del dataset e valore una lista di liste, lista[0] = nomi var continue, lista[1] = nomi var discrete
with open('../dataset/dict_names.pickle', 'rb') as handle:
    columns_type_dataset = pickle.load(handle)

#lista dei nomi delle black box
blackbox_list = ['rf', 'svm', 'mlp']

In [4]:
alpha_list = np.linspace(0,1,11)
beta_list = 1-alpha_list

for idx, dataset in enumerate(dataset_list):
    
    outfile = gzip.open('../output/%s_alphabeta.json.gzip' % dataset, 'wb') 
    
    print(datetime.datetime.now(), 'dataset: %s' % dataset)
    df_2e = pd.read_csv('../dataset/%s_2e.csv' % dataset)
    print('number of instances in the dataset: %s' % len(df_2e))
    print()
    
    cols_Y = [col for col in df_2e.columns if col.startswith(columns_ylist[idx])]
    cols_X = [col for col in df_2e.columns if col not in cols_Y]
    
    X2e = df_2e[cols_X].values
    y2e = df_2e[cols_Y].values
    
    cols_Y_BB = ['BB_'+str(col) for col in cols_Y]
    #print(cols_Y_BB)
    
    for blackbox_name in blackbox_list:
        
        print(datetime.datetime.now(), '\tblack box: %s' % blackbox_name)
        bb = pickle.load(gzip.open('../models/%s_%s.pickle.gz' % (blackbox_name, dataset), 'rb'))
        y_bb = bb.predict(X2e)
        
        #creo test set con label dati dalla black box (mi dimentico dei label reali)
        BB_predictions_df = pd.DataFrame(y_bb,columns=cols_Y_BB)
        Xtest_features_df = pd.DataFrame(X2e,columns=cols_X)
        #dataframe to explain
        X2E = pd.concat([Xtest_features_df,BB_predictions_df],axis=1)
        X2E = X2E.sample(n=200,random_state=0)
        
        for instance in X2E.index.values:
                        
            #istanza da spiegare
            i2e = X2E.loc[instance] 
            i2e_values = i2e[cols_X].values
            y_i2e_bb = bb.predict(i2e_values.reshape(1, -1))
        
            #print(datetime.datetime.now(), '\tdistance function in feature space, black box: %s' % blackbox_name)
            #variabili discrete: le features discrete
            #variabili continue: le feature continue
            #classi: le classi (target)
            X2E_wdistances = distance_functions.sorted_distances_df(X2E,i2e,discrete_var=X2E[columns_type_dataset[dataset][1]].columns.values,continuous_var=X2E[columns_type_dataset[dataset][0]].columns.values,classes_name=X2E[cols_Y_BB].columns.values,label_distance='feat_space_dist')
        
            #print(datetime.datetime.now(), '\tdistance function in label space, black box: %s' % blackbox_name)
            #variabili discrete: le classi (target)
            #variabili continue: nessuna (non conto le features per questa distanza)
            #classi: variabili da ignorare presenti nel dataset perchè è otuput dell'applicazione della stessa funzione
            X2E_wdistances = distance_functions.sorted_distances_df(X2E_wdistances,i2e,discrete_var=X2E[cols_Y_BB].columns.values, continuous_var=[], classes_name=['feat_space_dist','old_index_feat_space_dist'],label_distance='label_space_dist')
        
            mixed_discrete = np.append(X2E[columns_type_dataset[dataset][1]].columns.values,X2E[cols_Y_BB].columns.values)        
            #print(datetime.datetime.now(), '\tdistance function in mixed space, black box: %s' % blackbox_name)
            #variabili discrete: le features discrete + le classi (target) 
            #variabili continue: le feature continue
            #classi: variabili da ignorare presenti nel dataset perchè è otuput dell'applicazione della stessa funzione
            X2E_wdistances = distance_functions.sorted_distances_df(X2E_wdistances,i2e,discrete_var=mixed_discrete,continuous_var=X2E[columns_type_dataset[dataset][0]].columns.values,classes_name=['old_index_label_space_dist','old_index_feat_space_dist','feat_space_dist','label_space_dist'],label_distance='mixed_space_dist')
        
            filter_old_indexes = [i for i in X2E_wdistances.columns.values if 'index' in i]
            k = int(0.5*sqrt(len(X2E_wdistances))) #primi vicini da prendere
            size= 1000 #vicini sintetici da generare
        
            #sample kNN for synthetic neighborhood based on feature space distances
            filters_features_space = filter_old_indexes.copy()
            filters_features_space.append('label_space_dist') 
            filters_features_space.append('mixed_space_dist') 
            sampleKnn_feat_space = X2E_wdistances.drop(filters_features_space,1).sort_values(by='feat_space_dist').reset_index().drop('index',1).loc[0:k]
        
            #sample kNN for synthetic neighborhood based on label space distances
            filters_label_space = filter_old_indexes.copy()
            filters_label_space.append('feat_space_dist') 
            filters_label_space.append('mixed_space_dist') 
            sampleKnn_label_space = X2E_wdistances.drop(filters_label_space,1).sort_values(by='label_space_dist').reset_index().drop('index',1).loc[0:k]
            
            #sample kNN for synthetic neighborhood based on mixed space distances
            filters_mixed_space = filter_old_indexes.copy()
            filters_mixed_space.append('feat_space_dist') 
            filters_mixed_space.append('label_space_dist') 
            sampleKnn_mixed_space = X2E_wdistances.drop(filters_mixed_space,1).sort_values(by='mixed_space_dist').reset_index().drop('index',1).loc[0:k]
        
            #####################################################################################################
            #####################################################################################################
            ##Creo dataset sintetico n1: unisco il sample dei k primi vicini nello spazio delle feat. e dei label
            #print(datetime.datetime.now(), '\tsynthetic neighborhood alpha/beta, dataset %s, black box: %s' % (dataset, blackbox_name))
            # alpha: percentuale di neighbours che voglio dai vicini nello spazio delle features
            # beta: percentuale di neighbours che voglio dai vicini nello spazio dei labels
            for alpha,beta in zip(alpha_list,beta_list):
                
                alpha_beta_sample_knn = synthetic_neighborhood.sample_alphaFeat_betaLabel(sampleKnn_feat_space.drop('feat_space_dist',1),sampleKnn_label_space.drop('label_space_dist',1),alpha=round(alpha,1),beta=round(beta,1))
                synthetic_neighborhood1 = synthetic_neighborhood.random_synthetic_neighborhood_df(alpha_beta_sample_knn,size,discrete_var=X2E[columns_type_dataset[dataset][1]].columns.values,continuous_var=X2E[columns_type_dataset[dataset][0]].columns.values,classes_name=cols_Y_BB)
            
                #uso la black box per assegnare una predizione ad ogni istanza sintetica
                BB_label_syn1_df = pd.DataFrame(bb.predict(synthetic_neighborhood1.values),columns=cols_Y_BB)
                synthetic_neighborhood1 = pd.concat([synthetic_neighborhood1,BB_label_syn1_df],1)
            
                #####################################################################################################
                #faccio crescere un alberto decisionale su questo vicinato sintetico
                tree1 = DecisionTreeClassifier()
                tree1.fit(synthetic_neighborhood1.drop(cols_Y_BB,1).values,synthetic_neighborhood1[cols_Y_BB].values)
                print('____EVALUATION TREE alpha-beta___ bb: %s' % blackbox_name)
                ## evuluating on synthetic neighborhood
                y_syn1 = synthetic_neighborhood1[cols_Y_BB].values
                y_tree1_syn1 = tree1.predict(synthetic_neighborhood1.drop(cols_Y_BB,1).values)
                f1_syn1_tree1 = f1_score(y_true=y_syn1,y_pred=y_tree1_syn1, average='micro')
                ## evuluating on real kNN neighborhood used to create the synthetic one
                y_samplekNN1 = bb.predict(alpha_beta_sample_knn.drop(cols_Y_BB,1).values)
                y_tree1_kNN1 = tree1.predict(alpha_beta_sample_knn.drop(cols_Y_BB,1).values)
                f1_kNN1_tree1 = f1_score(y_true=y_samplekNN1,y_pred=y_tree1_kNN1, average='micro')
                #hit
                y_hit_tree1 = tree1.predict(i2e_values.reshape(1, -1))
                hit_jc_tree1 = jaccard_similarity_score(y_i2e_bb,y_hit_tree1)
                hit_sm_tree1 = distance_functions.simple_match_distance(y_i2e_bb[0],y_hit_tree1[0])
                #rule tree1
                rule_tree1,len_rule1 = rules.istance_rule_extractor(i2e_values.reshape(1, -1),tree1,cols_X)
            
                print('\t  F1-score tree1 on synthetic neighborhood: %.4f' % f1_syn1_tree1)
                print('\t  F1-score tree1 on kNN sample used to generate synthetic neigh.: %.4f' % f1_kNN1_tree1)
                print('\t "hit" of tree1 on i2e[%d], evaluated with the simple match distance: %.4f' % (instance,hit_sm_tree1))
                print('\t "hit" of tree1 on i2e[%d], evaluated with the jaccard similarity: %.4f' % (instance,hit_jc_tree1))
                print('\t Decision Rule for i2e, tree 1: %s, lenght: %d' % (str(rule_tree1),len_rule1))
                print()
            
            
                jrow = {
                    'alpha':str(round(alpha,2)),
                    'beta':str(round(beta,2)),
                    'dataset_name':dataset,
                    'bb_name': blackbox_name,
                    'i2e_id': str(instance),
                    'fidelity_tree1_syn':str(f1_syn1_tree1),
                    'fidelity_tree1_kNN':str(f1_kNN1_tree1),
                    'i2e_bb_label': y_i2e_bb[0].astype(int).tolist(),
                    'i2e_tree1_label':y_hit_tree1[0].astype(int).tolist(),
                    'hit_sm_tree1':str(hit_sm_tree1),
                    'hit_jc_tree1':str(hit_jc_tree1),
                    'rule_tree1':rule_tree1,
                    'lenght_rule_tree1':str(int(len_rule1)),
                }
            
                json_str = ('%s\n' % json.dumps(jrow)).encode('utf-8')
                outfile.write(json_str)
            
            if idx % 10 == 0:
                print(datetime.datetime.now(), idx)
                outfile.flush()
                
    outfile.close()
    print()
    print()

2018-10-29 19:50:53.466387 dataset: yeast
number of instances in the dataset: 726

2018-10-29 19:50:53.498797 	black box: rf
____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 251
leaf node 251 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.8364
	 "hit" of tree1 on i2e[571], evaluated with the simple match distance: 0.0714
	 "hit" of tree1 on i2e[571], evaluated with the jaccard similarity: 0.7500
	 Decision Rule for i2e, tree 1: Att61=-0.26 <= -0.14, Att25=0.1 > 0.05, Att15=0.15 > 0.03, Att62=-0.29 <= -0.06, Att46=0.05 > -0.08, Att51=-0.09 > -0.13, Att60=-0.14 <= -0.07, Att75=-0.04 <= 0.16, Att9=-0.0 <= 0.0, Att90=-0.05 > -0.09, Att100=-0.04 > -0.07 -> [0. 0. 0. 1. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 11

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 170
leaf node 170 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN s

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 32
leaf node 32 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 1.0000
	 "hit" of tree1 on i2e[571], evaluated with the simple match distance: 0.0000
	 "hit" of tree1 on i2e[571], evaluated with the jaccard similarity: 1.0000
	 Decision Rule for i2e, tree 1: Att73=0.06 > -0.02, Att35=0.09 > -0.14, Att96=-0.02 <= 0.05, Att92=-0.02 > -0.1, Att24=0.11 > 0.03, Att12=-0.04 <= 0.13, Att6=-0.03 <= 0.15, Att21=0.16 <= 0.28, Att68=-0.19 <= 0.06, Att54=0.0 > -0.07, Att25=0.1 > 0.02, Att61=-0.26 <= -0.13, Att15=0.15 > -0.01, Att38=0.14 > -0.02 -> [0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 14

2018-10-29 19:50:59.248027 0
____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 175
leaf node 175 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 224
leaf node 224 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.7556
	 "hit" of tree1 on i2e[498], evaluated with the simple match distance: 0.0714
	 "hit" of tree1 on i2e[498], evaluated with the jaccard similarity: 0.6667
	 Decision Rule for i2e, tree 1: Att87=-0.1 <= -0.02, Att96=0.25 > 0.12, Att86=-0.04 <= 0.0, Att19=-0.0 > -0.07, Att20=-0.06 > -0.19, Att7=0.11 <= 0.16, Att31=0.12 > 0.05, Att39=0.06 <= 0.14, Att33=-0.01 <= 0.13, Att25=-0.11 > -0.19, Att73=-0.01 <= 0.02, Att27=0.08 > 0.01, Att71=-0.02 <= 0.16, Att42=-0.06 > -0.1, Att97=0.08 <= 0.28, Att77=0.19 > -0.03, Att31=0.12 <= 0.2, Att45=-0.07 <= 0.11, Att52=-0.09 > -0.22 -> [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 19

2018-10-29 19:51:05.067413 0
____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 567
leaf node 567 reached, no decision here
	  F1-score tree1

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 624
leaf node 624 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.7429
	 "hit" of tree1 on i2e[586], evaluated with the simple match distance: 0.0714
	 "hit" of tree1 on i2e[586], evaluated with the jaccard similarity: 0.0000
	 Decision Rule for i2e, tree 1: Att88=0.08 > -0.01, Att80=-0.06 <= -0.05, Att2=0.06 > -0.04, Att85=-0.06 <= -0.04, Att67=0.07 > -0.09, Att11=-0.0 <= 0.04, Att84=-0.11 <= 0.0 -> [0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.], lenght: 7

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 874
leaf node 874 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.6667
	 "hit" of tree1 on i2e[586], evaluated with the simple match distance: 0.0714
	 "hit" of tree1 on i2e[586], evaluated with the jaccard similarity: 0.5000
	 Deci

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 71
leaf node 71 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 1.0000
	 "hit" of tree1 on i2e[457], evaluated with the simple match distance: 0.0000
	 "hit" of tree1 on i2e[457], evaluated with the jaccard similarity: 1.0000
	 Decision Rule for i2e, tree 1: Att61=-0.29 <= -0.13, Att15=0.12 > 0.04, Att91=-0.06 <= 0.05, Att25=0.08 > 0.02, Att90=-0.06 > -0.18, Att67=-0.0 <= 0.06, Att21=0.1 > -0.11, Att66=-0.01 > -0.17, Att75=0.04 > -0.07, Att69=0.03 > -0.21, Att10=0.12 > -0.06, Att58=-0.17 <= -0.05, Att30=0.05 <= 0.16, Att37=0.12 > -0.1, Att64=-0.09 <= 0.02, Att68=-0.06 <= 0.06, Att91=-0.06 > -0.13, Att29=0.13 > 0.02 -> [0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 18

____EVALUATION TREE alpha-beta___ bb: rf
id leaf node: 34
leaf node 34 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree

...

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 668
leaf node 668 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.6122
	 "hit" of tree1 on i2e[495], evaluated with the simple match distance: 0.0000
	 "hit" of tree1 on i2e[495], evaluated with the jaccard similarity: 1.0000
	 Decision Rule for i2e, tree 1: Att102=0.7 > 0.02, Att57=-0.0 <= 0.02, Att102=0.7 > 0.16, Att69=0.03 > -0.01, Att74=-0.02 > -0.16, Att73=-0.01 <= 0.09, Att94=0.0 <= 0.16, Att95=-0.01 > -0.14, Att97=-0.01 > -0.13, Att88=-0.02 > -0.11, Att28=0.01 > -0.2, Att53=-0.07 > -0.19, Att18=0.02 > -0.23, Att57=-0.0 <= 0.02, Att31=0.11 <= 0.22, Att62=-0.01 <= 0.17, Att75=0.01 <= 0.03, Att102=0.7 > 0.18, Att5=0.12 <= 0.25, Att86=0.01 > -0.21, Att80=0.0 <= 0.13, Att90=-0.02 <= 0.24, Att83=-0.01 > -0.2, Att39=0.06 <= 0.18, Att65=-0.01 > -0.1, Att6=0.06 <= 0.08, Att57=-0.0 <= 0.02, Att37=0.07 > -0.1, Att13=0.06 > -0.17, Att49=0

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 984
leaf node 984 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.5217
	 "hit" of tree1 on i2e[716], evaluated with the simple match distance: 0.1429
	 "hit" of tree1 on i2e[716], evaluated with the jaccard similarity: 0.0000
	 Decision Rule for i2e, tree 1: Att3=0.05 > -0.02, Att37=-0.14 <= -0.01, Att34=-0.03 > -0.07, Att63=0.04 > 0.01, Att69=-0.14 > -0.2, Att29=-0.13 <= 0.01, Att23=-0.18 <= -0.09, Att79=0.16 > 0.03, Att84=-0.04 > -0.1, Att60=0.19 > -0.11, Att79=0.16 > 0.06, Att37=-0.14 > -0.2, Att87=0.01 <= 0.03 -> [1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0.], lenght: 13

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 413
leaf node 413 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.4898
	 "hit" of tree1 on i2e[716], evaluated

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 1042
leaf node 1042 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.6567
	 "hit" of tree1 on i2e[202], evaluated with the simple match distance: 0.2857
	 "hit" of tree1 on i2e[202], evaluated with the jaccard similarity: 0.3333
	 Decision Rule for i2e, tree 1: Att3=-0.01 > -0.02, Att57=0.15 > -0.02, Att69=0.15 > 0.09, Att20=0.1 > -0.05, Att81=-0.02 <= 0.05, Att82=-0.05 <= 0.05, Att79=-0.06 <= -0.04, Att62=0.22 > 0.0, Att103=0.12 > 0.04, Att55=-0.08 > -0.12, Att64=0.02 <= 0.03 -> [0. 0. 0. 0. 1. 1. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 11

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 906
leaf node 906 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.8358
	 "hit" of tree1 on i2e[202], evaluated with the simple match distance: 0.0000

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 783
leaf node 783 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.8197
	 "hit" of tree1 on i2e[165], evaluated with the simple match distance: 0.0714
	 "hit" of tree1 on i2e[165], evaluated with the jaccard similarity: 0.7500
	 Decision Rule for i2e, tree 1: Att53=0.23 > -0.11, Att79=0.1 > 0.03, Att89=0.23 > -0.01, Att74=-0.09 > -0.19, Att7=-0.16 <= 0.16, Att91=0.21 > -0.19, Att13=-0.06 <= 0.15, Att38=-0.06 > -0.12, Att1=-0.12 <= 0.16, Att84=0.18 <= 0.23, Att92=-0.06 <= 0.29, Att29=-0.0 > -0.05, Att46=-0.11 <= -0.11, Att11=0.01 <= 0.03, Att13=-0.06 > -0.12 -> [1. 0. 0. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 15

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 845
leaf node 845 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.8

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 589
leaf node 589 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.7778
	 "hit" of tree1 on i2e[250], evaluated with the simple match distance: 0.0000
	 "hit" of tree1 on i2e[250], evaluated with the jaccard similarity: 1.0000
	 Decision Rule for i2e, tree 1: Att3=0.13 > -0.02, Att53=-0.08 <= 0.05, Att91=0.01 <= 0.06, Att13=0.23 > -0.02, Att89=-0.08 <= -0.06, Att79=0.05 <= 0.13, Att81=0.19 > -0.12, Att58=-0.1 <= 0.02, Att69=-0.02 > -0.07, Att60=-0.14 <= -0.09, Att78=-0.0 <= 0.09 -> [1. 1. 1. 0. 0. 0. 0. 0. 0. 0. 0. 1. 1. 0.], lenght: 11

____EVALUATION TREE alpha-beta___ bb: mlp
id leaf node: 867
leaf node 867 reached, no decision here
	  F1-score tree1 on synthetic neighborhood: 1.0000
	  F1-score tree1 on kNN sample used to generate synthetic neigh.: 0.7463
	 "hit" of tree1 on i2e[250], evaluated with the simple match distance: 0.07